### Derive feature from other features

Features can also be created based on other features. 

In this tutorial we will create a feature that measures the Z-Score of the Latest invoice Amount for the customer compared to that customer's invoices over a 28d period. This feature is derived from 3 features we created previously: CUSTOMER_Latest_invoice_Amount, CUSTOMER_Avg_of_invoice_Amount_28d and CUSTOMER_Std_of_invoice_Amount_28d.

In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

16:43:20 | INFO     | Using configuration file at: /Users/viktor/.featurebyte/config.yaml
16:43:20 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)
16:43:20 | INFO     | SDK version: 0.6.0.dev121
16:43:20 | INFO     | No catalog activated.
16:43:20 | INFO     | 10 feature lists, 59 features deployed
16:43:20 | INFO     | Using profile: tutorial
16:43:21 | INFO     | Using configuration file at: /Users/viktor/.featurebyte/config.yaml
16:43:21 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)
16:43:21 | INFO     | SDK version: 0.6.0.dev121
16:43:21 | INFO     | No catalog activated.
16:43:21 | INFO     | 10 feature lists, 59 features deployed
16:43:21 | INFO     | Catalog activated: Grocery Dataset Tutorial


#### Get features we previously created and saved

In [2]:
customer_latest_invoice_amount = catalog.get_feature("CUSTOMER_Latest_invoice_Amount")
customer_avg_of_invoice_amount_28d = catalog.get_feature("CUSTOMER_Avg_of_invoice_Amount_28d")
customer_std_of_invoice_amount_28d = catalog.get_feature("CUSTOMER_Std_of_invoice_Amount_28d")

#### Derive a z-score feature from saved features

In [3]:
customer_latest_invoice_amount_Z_score_to_invoice_amount_28d = (
    customer_latest_invoice_amount
    - customer_avg_of_invoice_amount_28d
) / customer_std_of_invoice_amount_28d
# Give a name to new feature
customer_latest_invoice_amount_Z_score_to_invoice_amount_28d.name = \
"CUSTOMER_Latest_invoice_Amount_Z_Score_to_invoice_Amount_28d"

#### Preview feature


In [4]:
customer_latest_invoice_amount_Z_score_to_invoice_amount_28d.primary_entity

 {
   'name': 'customer',
   'created_at': '2023-11-27T15:39:09.477000',
   'updated_at': '2023-11-27T15:39:19.968000',
   'description': None,
   'serving_names': [
     'GROCERYCUSTOMERGUID'
   ],
   'catalog_name': 'Grocery Dataset Tutorial'
 }]

In [5]:
# Get observation table: 'Preview Table with 10 Customers'
preview_table = catalog.get_observation_table("Preview Table with 10 Customers").to_pandas()

In [6]:
# Preview CUSTOMER_Age
customer_latest_invoice_amount_Z_score_to_invoice_amount_28d.preview(preview_table)

POINT_IN_TIME                   GROCERYCUSTOMERGUID  \
0 2022-11-28 11:36:31  d4559f7d-eb28-42c6-b47d-847de24952c2   
1 2022-10-09 15:47:55  3f8c7c4c-f2c2-408e-a08e-622de3d3a0b9   
2 2022-09-14 15:42:42  35390325-8443-43c1-a934-18db923d9a47   
3 2022-12-26 18:39:46  4eb4ee84-ee13-4eec-9c26-61b6eb4ba35b   
4 2022-12-06 08:47:43  e42fa5f3-7737-4c6a-9ef4-856f113e60bd   
5 2022-11-09 12:14:40  8440debb-6abc-4adc-8c6c-749928141fd0   
6 2022-10-12 17:32:15  8a54e527-e9a4-47a9-a28f-8b3c6ecc02db   
7 2023-01-01 11:51:28  cea213d4-36e4-48c3-ae8d-c7a25911e11c   
8 2023-02-05 15:48:23  3b4f2821-b761-40e9-a32a-5f09685cc597   
9 2023-03-10 16:15:46  91a64566-e212-4e36-8f23-c1f1f324a301   

   CUSTOMER_Latest_invoice_Amount_Z_Score_to_invoice_Amount_28d  
0                                                NaN             
1                                                NaN             
2                                          -0.838057             
3                                           0.992653             
4                                           1.530644             
5                                                NaN             
6                                          -0.049459             
7                                          -0.530470             
8                                           0.024855             
9                                          -0.743774

#### Save feature

In [7]:
customer_latest_invoice_amount_Z_score_to_invoice_amount_28d.save()

Done! |████████████████████████████████████████| 100% in 6.5s (0.16%/s)         


#### Add description and view definition file 

In [8]:
# Add description
customer_latest_invoice_amount_Z_score_to_invoice_amount_28d.update_description(
	"Z-Score of the Latest invoice Amount for the customer compared to customer invoices over a 28d period"
)
# See feature definition file
customer_latest_invoice_amount_Z_score_to_invoice_amount_28d.definition

'# Generated by SDK version: 0.6.0.dev121\nfrom bson import ObjectId\nfrom featurebyte import ColumnCleaningOperation\nfrom featurebyte import DisguisedValueImputation\nfrom featurebyte import EventTable\nfrom featurebyte import FeatureJobSetting\nfrom featurebyte import ValueBeyondEndpointImputation\n\n\n# event_table name: "GROCERYINVOICE"\nevent_table = EventTable.get_by_id(ObjectId("6564b7ebbeba6c193e0fe3bc"))\nevent_view = event_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[\n        ColumnCleaningOperation(\n            column_name="Amount",\n            cleaning_operations=[\n                DisguisedValueImputation(\n                    imputed_value=None, disguised_values=[-99.0, -98.0]\n                ),\n                ValueBeyondEndpointImputation(\n                    type="less_than", end_point=0.0, imputed_value=0.0\n                ),\n                ValueBeyondEndpointImputation(\n                    type="greater_than", end_point=2000.0, imputed_value=2000.0\n                ),\n            ],\n        )\n    ],\n)\ngrouped = event_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).aggregate_over(\n    value_column="Amount",\n    method="latest",\n    windows=[None],\n    feature_names=["CUSTOMER_Latest_invoice_Amount"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", frequency="3600s", time_modulo_frequency="120s"\n    ),\n    skip_fill_na=True,\n)\nfeat = grouped["CUSTOMER_Latest_invoice_Amount"]\ngrouped_1 = event_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).aggregate_over(\n    value_column="Amount",\n    method="avg",\n    windows=["28d"],\n    feature_names=["CUSTOMER_Avg_of_invoice_Amount_28d"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", frequency="3600s", time_modulo_frequency="120s"\n    ),\n    skip_fill_na=True,\n)\nfeat_1 = grouped_1["CUSTOMER_Avg_of_invoice_Amount_28d"]\ngrouped_2 = event_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).aggregate_over(\n    value_column="Amount",\n    method="std",\n    windows=["28d"],\n    feature_names=["CUSTOMER_Std_of_invoice_Amount_28d"],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", frequency="3600s", time_modulo_frequency="120s"\n    ),\n    skip_fill_na=True,\n)\nfeat_2 = grouped_2["CUSTOMER_Std_of_invoice_Amount_28d"]\nfeat_3 = (feat - feat_1) / feat_2\nfeat_3.name = "CUSTOMER_Latest_invoice_Amount_Z_Score_to_invoice_Amount_28d"\noutput = feat_3\noutput.save(_id=ObjectId("6564b91c69ee318ce739930c"))\n'

### Concepts in this tutorial
- [Feature Transforms](https://docs.featurebyte.com/latest/about/glossary/#feature-transforms)

#### SDK reference for
- [Catalog.get_feature()](https://docs.featurebyte.com/latest/reference/featurebyte.api.catalog.Catalog.get_feature/)